In [ ]:
###############################################                  FC_LEA : Scrapping project             ######################################

In [ ]:
import requests
import pandas as pd
import re
from bs4 import BeautifulSoup
from datetime import datetime
import os
import matplotlib.pyplot as plt
import matplotlib.dates as mdates

In [ ]:
# On commence le svcraping et le nettoyage des données collectées ainsi que la transformation en fichier excel pour les élections danoises
# Les même principes seront utilisés pour les élections tchèques avec quelques spécificités à la vue du nombre plus important d'URLs
# Liste des pages Wikipedia contenant les sondages pour les élections générales danoises

urls = [
    "https://en.wikipedia.org/wiki/Opinion_polling_for_the_2015_Danish_general_election",
    "https://en.wikipedia.org/wiki/Opinion_polling_for_the_2019_Danish_general_election",
    "https://en.wikipedia.org/wiki/Opinion_polling_for_the_2022_Danish_general_election"
]

# Définition des partis et leurs orientations politiques manuellement

party_leanings = {
    'A': 'gauche',
    'V': 'droite',
    'O': 'droite',
    'B': 'centre',
    'F': 'gauche',
    'Ø': 'extrême gauche',
    'I': 'droite',
    'C': 'centre-droite',
    'K': 'centre',
    'Å': 'gauche',
    'D': 'droite',
    'P': 'gauche',
    'Q': 'centre',
    'M': 'centre',
    'G': 'gauche'
}

# On définit une fonction qui va gérer les en-têtes de colonnes qui peuvent être des tuples ou chaînes complexes

def extract_party_key(column_name):

    # Si c’est un tuple ou une liste (souvent dans pd.read_html avec multi-index)

    if isinstance(column_name, tuple) or isinstance(column_name, list):

        # Formatage

        if len(column_name) > 0:
            first_element = str(column_name[0]).strip()
            if first_element in party_leanings:
                return first_element                          # Retourne la lettre si elle est valide

            for element in column_name:
                element_str = str(element).strip()
                if element_str in party_leanings:
                    return element_str                        # Retourne la première lettre valide trouvée

# Cela permet d'attribuer un nom aux partis qui n'ont pas été trouvés

    # Si c’est une chaîne simple, on fait comme suit

    col_str = str(column_name).strip()

    # Extraction d'un code de parti si il est valide et utilisable

    for party_code in party_leanings.keys():
        if party_code == col_str or (len(party_code) == 1 and party_code in col_str):
            return party_code                                 # Retourne si correspondance exacte ou lettre incluse

    return col_str                                            # Retourne la chaîne brute s'il n'y a pas de correspondance

# Ici on crée un dictionnaire qui va recensé tous les scores finaux des différents partis danois

final_results = {
    '2015': {
        'A': 26.3, 'V': 19.5, 'O': 21.1, 'B': 4.6, 'F': 4.2, 'Ø': 7.8, 'I': 7.5, 'C': 3.4, 'K': 0.8, 'Å': 4.8
    },
    '2019': {
        'A': 25.9, 'V': 23.4, 'O': 8.7, 'B': 8.6, 'F': 2.3, 'Ø': 6.9, 'I': 2.4, 'C': 6.6, 'K': 1.7, 'D': 2.4, 'Å': 3.0, 'P': 2.4
    },
    '2022': {
        'A': 27.5, 'V': 13.3, 'C': 5.5, 'O': 2.6, 'B': 7.9, 'F': 3.0, 'Ø': 5.1, 'I': 1.8, 'Å': 3.3, 'D': 8.1, 'Q': 3.4, 'M': 9.3, 'G': 3.8
    }
}

# Encore une fois on convertit les dates au format année-mois-jour

def standardize_date(date_str, year):

    # S’assurer que date_str est une chaîne de caractères

    date_str = str(date_str)

    # On mentionne les différents formats possibles dans les tableaux

    months = {
        'Jan': '01', 'Feb': '02', 'Mar': '03', 'Apr': '04', 'May': '05', 'Jun': '06',
        'Jul': '07', 'Aug': '08', 'Sep': '09', 'Oct': '10', 'Nov': '11', 'Dec': '12'
    }

    try:

        # Pour les dates s'étalant sur plusieurs jours (plages), on les standardise

        if '-' in date_str and not any(month in date_str for month in months.keys()):
            parts = date_str.split('-')
            if len(parts) > 1:
                end_date = parts[1].strip()

                # Si c’est juste un jour, on ajoute le mois

                if end_date.isdigit():
                    month_part = date_str.split(' ')
                    if len(month_part) > 1:
                        date_str = end_date + ' ' + month_part[-1]

        # Extraction du jour et du mois avec la bibliothèque native regex

        day_pattern = r'(\d{1,2})'
        month_pattern = r'(Jan|Feb|Mar|Apr|May|Jun|Jul|Aug|Sep|Oct|Nov|Dec)'

        day_match = re.search(day_pattern, date_str)
        month_match = re.search(month_pattern, date_str)

        if day_match and month_match:
            day = day_match.group(1).zfill(2)  # Ajout du 0 précédent le nombre actuel
            month = months[month_match.group(1)]
            return f"{year}-{month}-{day}"     # Format ISO
        else:

            # Si seul le mois est présent, utiliser le 1er du mois

            if month_match:
                month = months[month_match.group(1)]
                return f"{year}-{month}-01"
            else:
                return f"{year}-01-01"  # Par défaut, 1er janvier
    except Exception as e:
        print(f"Erreur dans standardize_date: {e}, date_str: {date_str}")
        return f"{year}-01-01"          # Même valeur par défaut en cas d’erreur

# Permet de contenir les données au format "long" avant conversion en DataFrame

all_rows = []

# Permettra de suivre l'index dans le tableau final

row_index = 1

# Boucle principale pour scraper les données pour chaque URL

for url in urls:
    try:
        # Extraire l’année de l’URL

        year_match = re.search(r'(\d{4})_Danish_general_election', url)
        year = year_match.group(1) if year_match else None

        print(f"Traitement de l’URL pour {year}: {url}")

        # Lire les tableaux de l’URL avec pandas

        tables = pd.read_html(url)
        print(f"Nombre de tableaux trouvés: {len(tables)}")

        # Trouver les tableaux pertinents contenant des données de sondage
        e
        found_table = False

        # BNouvelle boucle sur chaque tableau trouvé

        for i, table in enumerate(tables):
            try:
                if not isinstance(table, pd.DataFrame):
                    continue

                print(f"Examen du tableau {i+1}, colonnes: {table.columns.tolist()}")

                # Assouplissement des conditions de détection du tableau

                if not any(term in str(col).lower() for col in table.columns for term in ['poll', 'firm', 'date', 'institute']):
                    if len(table.columns) < 3:                         # Tableau trop petit
                        continue

                # Fonction pour trouver une colonne par mots-clés

                def find_column(keywords):
                    for col in table.columns:
                        col_str = str(col).lower()
                        if any(keyword in col_str for keyword in keywords):
                            return col
                    return None

                # Identification des colonnes pertinentes

                polling_firm_col = find_column(['poll', 'firm', 'institute'])
                date_col = find_column(['date', 'field'])
                sample_size_col = find_column(['sample', 'size'])

                if not (polling_firm_col and date_col):
                    continue                               # Passer au tableau suivant si les colonnes clés sont absentes

                print(f"Colonnes identifiées: polling_firm={polling_firm_col}, date={date_col}, sample_size={sample_size_col}")

                # Boucle sur chaque ligne du tableau

                for index, row in table.iterrows():
                    try:
                        polling_firm = str(row[polling_firm_col])

                        # Extraire et standardiser la date

                        date_str = str(row[date_col])
                        polling_date = standardize_date(date_str, year)

                        # Extraire la taille de l’échantillon

                        sample_size = str(row[sample_size_col]) if sample_size_col and sample_size_col in row else 'N/A'

                        # Boucle sur chaque colonne pour trouver les partis

                        for col in table.columns:

                            col_str = str(col).lower()            # Ignorer les colonnes qui sont encore non liées aux partis
                            if col in [polling_firm_col, date_col, sample_size_col] or any(term in col_str for term in ['turnout', 'lead', 'others', 'poll', 'date', 'sample']):
                                continue

                            # Vérifier si la valeur est numérique

                            try:
                                value = row[col]
                                if pd.isna(value):
                                    continue

                                # Convertir en valeur décimale si c'est le cas

                                try:
                                    result = float(value)
                                except (ValueError, TypeError):
                                                         # Traitement de la valeur si c’est une chaîne
                                    if isinstance(value, str):
                                        value = value.replace('%', '').replace(',', '.').strip()
                                        try:
                                            result = float(value)
                                        except:
                                            continue
                                    else:
                                        continue

                                # Extraire le code du parti

                                party_key = extract_party_key(col)

                                # Déterminer l’orientation politique

                                political_leaning = party_leanings.get(party_key, 'Non catégorisé')

                                # Obtenir le résultat final

                                final_result = final_results.get(year, {}).get(party_key, None)

                                # Créer une ligne au format souhaité

                                new_row = {
                                    'year': year,
                                    'polling_firm': polling_firm,
                                    'polling_date': polling_date,
                                    'political_party': party_key,
                                    'political_leaning': political_leaning,
                                    'result': result,
                                    'sample_size': sample_size,
                                    'final_result': final_result
                                }

                                all_rows.append(new_row)
                                row_index += 1
                            except Exception as e:
                                print(f"Erreur lors du traitement de la colonne {col}: {e}")
                                continue
                    except Exception as e:
                        print(f"Erreur lors du traitement de la ligne {index}: {e}")
                        continue

                found_table = True
                print(f"Tableau {i+1} traité avec succès")
                break                                    # Sortir après avoir trouvé un tableau pertinent

            except Exception as e:
                print(f"Erreur lors du traitement du tableau {i+1}: {e}")
                continue

        if not found_table:
            print(f"Aucun tableau pertinent trouvé pour {url}")

    except Exception as e:
        print(f"Erreur lors du traitement de l’URL {url}: {e}")
        continue

# Création du Dataframe finales des données traitées au dessus

if all_rows:
    final_df = pd.DataFrame(all_rows)

    # Trier par date et parti par ordre chronologique

    final_df = final_df.sort_values(['polling_date', 'political_party'])

    # Réinitialiser l’index pour rendre la numérotation propre

    final_df = final_df.reset_index(drop=True)
    final_df.index += 1                                         # Commencer à 1 au lieu de 0

    # Créer un dictionnaire qui regroupe les partis par orientation politique

    political_leaning_parties = {}
    for party, leaning in party_leanings.items():
        if leaning not in political_leaning_parties:
            political_leaning_parties[leaning] = []
        political_leaning_parties[leaning].append(party)

    # Afficher le dictionnaire des penchants politiques et les partis associés

    print("\nPartis par orientation politique:")
    for leaning, parties in political_leaning_parties.items():
        print(f"{leaning}: {', '.join(parties)}")

    # Configurer l’affichage pandas

    pd.set_option('display.max_rows', 20)
    pd.set_option('display.max_columns', None)
    pd.set_option('display.width', None)

final_df

Traitement de l’URL pour 2015: https://en.wikipedia.org/wiki/Opinion_polling_for_the_2015_Danish_general_election
Nombre de tableaux trouvés: 2
Erreur lors du traitement de l’URL https://en.wikipedia.org/wiki/Opinion_polling_for_the_2015_Danish_general_election: name 'e' is not defined
Traitement de l’URL pour 2019: https://en.wikipedia.org/wiki/Opinion_polling_for_the_2019_Danish_general_election
Nombre de tableaux trouvés: 9
Erreur lors du traitement de l’URL https://en.wikipedia.org/wiki/Opinion_polling_for_the_2019_Danish_general_election: name 'e' is not defined
Traitement de l’URL pour 2022: https://en.wikipedia.org/wiki/Opinion_polling_for_the_2022_Danish_general_election
Nombre de tableaux trouvés: 9
Erreur lors du traitement de l’URL https://en.wikipedia.org/wiki/Opinion_polling_for_the_2022_Danish_general_election: name 'e' is not defined


year          polling_firm polling_date                 political_party political_leaning  result sample_size  final_result
1     2015              Voxmeter   2015-03-02                               A            gauche    23.1         N/A          26.3
2     2015              Voxmeter   2015-03-02                               A            gauche    47.5         N/A          26.3
3     2015              Voxmeter   2015-03-02                               B            centre     7.8         N/A           4.6
4     2015              Voxmeter   2015-03-02                               C     centre-droite     5.3         N/A           3.4
5     2015              Voxmeter   2015-03-02                               F            gauche     6.9         N/A           4.2
6     2015              Voxmeter   2015-03-02                               I            droite     4.8         N/A           7.5
7     2015              Voxmeter   2015-03-02                               K            centre     0.3         N/A           0.8
8     2015              Voxmeter   2015-03-02                               O            droite    19.6         N/A          21.1
9     2015              Voxmeter   2015-03-02                               V            droite    22.3         N/A          19.5
10    2015              Voxmeter   2015-03-02                               V            droite    52.3         N/A          19.5
11    2015              Voxmeter   2015-03-02                               Å            gauche     1.2         N/A           4.8
12    2015              Voxmeter   2015-03-02                               Ø    extrême gauche     8.5         N/A           7.8
13    2015                Gallup   2015-03-05                               A            gauche    23.1         N/A          26.3
14    2015                Gallup   2015-03-05                               A            gauche    46.2         N/A          26.3
15    2015                Gallup   2015-03-05                               B            centre     6.9         N/A           4.6
16    2015                Gallup   2015-03-05                               C     centre-droite     5.3         N/A           3.4
17    2015                Gallup   2015-03-05                               F            gauche     6.0         N/A           4.2
18    2015                Gallup   2015-03-05                               I            droite     5.8         N/A           7.5
19    2015                Gallup   2015-03-05                               K            centre     1.0         N/A           0.8
20    2015                Gallup   2015-03-05                               O            droite    20.1         N/A          21.1
21    2015                Gallup   2015-03-05                               V            droite    21.1         N/A          19.5
22    2015                Gallup   2015-03-05                               V            droite    53.3         N/A          19.5
23    2015                Gallup   2015-03-05                               Å            gauche     1.8         N/A           4.8
24    2015                Gallup   2015-03-05                               Ø    extrême gauche     8.4         N/A           7.8
25    2015              Voxmeter   2015-03-08                               A            gauche    23.4         N/A          26.3
26    2015              Voxmeter   2015-03-08                               A            gauche    47.9         N/A          26.3
27    2015              Voxmeter   2015-03-08                               B            centre     7.5         N/A           4.6
28    2015              Voxmeter   2015-03-08                               C     centre-droite     4.8         N/A           3.4
29    2015              Voxmeter   2015-03-08                               F            gauche     6.4         N/A           4.2
30    2015              Voxmeter   2015-03-08                               I            droite     4.7   

In [ ]:
# Définir un mapping pour standardiser les noms des partis

party_name_mapping = {
    'A': 'A', 'Socialdemokraterne': 'A',
    'V': 'V', 'Venstre': 'V',
    'O': 'O', 'Dansk Folkeparti': 'O',
    'B': 'B', 'Radikale Venstre': 'B',
    'F': 'F', 'Socialistisk Folkeparti': 'F',
    'Ø': 'Ø', 'Enhedslisten': 'Ø',
    'I': 'I', 'Liberal Alliance': 'I',
    'C': 'C', 'Det Konservative Folkeparti': 'C',
    'K': 'K', 'Kristendemokraterne': 'K',
    'Å': 'Å', 'Alternativet': 'Å',
    'D': 'D', 'Nye Borgerlige': 'D',
    'P': 'P', 'Stram Kurs': 'P',
    'Q': 'Q', 'Frie Grønne': 'Q',
    'M': 'M', 'Moderaterne': 'M',
    'G': 'G', 'Grønne': 'G',
    'Others': 'Others', 'Oth.': 'Others', 'Oth': 'Others', 'Andet': 'Others', 'Other': 'Others',
    'others': 'Others', 'other': 'Others'
}

# Étape 1: Standardiser les noms des partis

final_df['political_party'] = final_df['political_party'].replace(party_name_mapping)

# Étape 2: Filtrer les lignes non liées aux sondages

keywords_to_remove = ['election', 'legislative', 'turnout', 'vote', 'ballot', 'result', 'official', 'final']
final_df_filtered = final_df[
    ~final_df['polling_firm'].str.lower().str.contains('|'.join(keywords_to_remove), na=False)
]

# Étape 3: Identifier les partis uniques

unique_parties = final_df_filtered['political_party'].unique()

# Étape 4: Créer un nouveau DataFrame au format wide

wide_data = []                                            # Liste pour stocker les données transformées
grouped = final_df_filtered.groupby(['polling_date', 'polling_firm', 'year', 'sample_size'], dropna=False)

# Boucle principale consistant à arcourir chaque groupe

for group_key, group in grouped:
    polling_date, polling_firm, year, sample_size = group_key  # Décomposer les clés présentes du groupe

    # Créer un dictionnaire avec les données communes à tous les partis pour ce sondage

    common_data = {
        'polling_date': polling_date,
        'polling_firm': polling_firm,
        'year': year,
        'sample_size': sample_size
    }

    # Créer un dictionnaire des données des partis

    party_results = {}

    # Boucle de boucle : Parcourir chaque ligne du groupe (chaque parti dans le sondage)
    for _, row in group.iterrows():
        party = row['political_party']

        # Condition pour éviter les doublons et privilégier les valeurs non nulles

        if party not in party_results or (pd.isna(party_results[party]['result']) and not pd.isna(row['result'])):
            party_results[party] = {
                'result': row['result'],                             # Résultat du sondage
                'final_result': row['final_result'],                 # Résultat officiel
                'political_leaning': row['political_leaning']        # Orientation politique
            }

    # Boucle de formatage qui ajoute les données de chaque parti

    for i, party in enumerate(unique_parties, start=1):
        if party in party_results:

            # Si le parti est présent dans ce sondage, ajout des données

            common_data[f'party{i}'] = party
            common_data[f'result{i}'] = party_results[party]['result']
            common_data[f'final_result{i}'] = party_results[party]['final_result']
            common_data[f'political_leaning{i}'] = party_results[party]['political_leaning']
        else:

            # Si le parti n’est pas dans ce sondage, on attribue au parti None

            common_data[f'party{i}'] = party
            common_data[f'result{i}'] = None
            common_data[f'final_result{i}'] = None
            common_data[f'political_leaning{i}'] = None

    # Ajouter le sondage transformé à la liste

    wide_data.append(common_data)

# Étape 5: Créer le DataFrame wide

wide2_df = pd.DataFrame(wide_data)

# Étape 6: Trier par année et date de sondage par ordre chronologique

wide2_df = wide2_df.sort_values(by=['year', 'polling_date'])

# Nous vérifions que le parti Others est bien inclus dans le résultat final

party_columns = [col for col in wide2_df.columns if col.startswith('party')]
others_rows = wide2_df[wide2_df[party_columns].eq('Others').any(axis=1)]

wide2_df

polling_date polling_firm  year sample_size party1  result1  final_result1 political_leaning1 party2  result2  final_result2 political_leaning2 party3  result3  final_result3 political_leaning3 party4  result4  final_result4 political_leaning4 party5  result5  final_result5 political_leaning5 party6  result6  final_result6 political_leaning6 party7  result7  final_result7 political_leaning7 party8  result8  final_result8 political_leaning8 party9  result9  final_result9 political_leaning9 party10  result10  final_result10 political_leaning10                         party11  result11  final_result11 political_leaning11 party12  result12  final_result12 political_leaning12                       party13  result13  final_result13 political_leaning13 party14  result14  final_result14 political_leaning14 party15  result15  final_result15 political_leaning15 party16  result16  final_result16 political_leaning16 party17  result17  final_result17 political_leaning17
0     2015-03-02     Voxmeter  2015         N/A      A     23.1           26.3             gauche      B      7.8            4.6             centre      C      5.3            3.4      centre-droite      F      6.9            4.2             gauche      I      4.8            7.5             droite      K      0.3            0.8             centre      O     19.6           21.1             droite      V     22.3           19.5             droite      Å      1.2            4.8             gauche       Ø       8.5             7.8      extrême gauche  ('Red', 'Unnamed: 19_level_1')       NaN             NaN                None       D       NaN             NaN                None  ('E', 'Unnamed: 14_level_1')       NaN             NaN                None       P       NaN             NaN                None       G       NaN             NaN                None       Q       NaN             NaN                None       M       NaN             NaN                None
1     2015-03-05       Gallup  2015         N/A      A     23.1           26.3             gauche      B      6.9            4.6             centre      C      5.3            3.4      centre-droite      F      6.0            4.2             gauche      I      5.8            7.5             droite      K      1.0            0.8             centre      O     20.1           21.1             droite      V     21.1           19.5             droite      Å      1.8            4.8             gauche       Ø       8.4             7.8      extrême gauche  ('Red', 'Unnamed: 19_level_1')       NaN             NaN                None       D       NaN             NaN                None  ('E', 'Unnamed: 14_level_1')       NaN             NaN                None       P       NaN             NaN                None       G       NaN             NaN                None       Q       NaN             NaN                None       M       NaN             NaN                None
2     2015-03-08     Voxmeter  2015         N/A      A     23.4           26.3             gauche      B      7.5            4.6             centre      C      4.8            3.4      centre-droite      F      6.4            4.2             gauche      I      4.7            7.5             droite      K      0.4            0.8             centre      O     18.7           21.1             droite      V     23.2           19.5             droite      Å      1.5            4.8             gauche       Ø       9.1             7.8      extrême gauche  ('Red', 'Unnamed: 19_level_1')       NaN             NaN                None       D       NaN             NaN                None  ('E', 'Unnamed: 14_level_1')       NaN             NaN                None       P       NaN             NaN                None       G       NaN             NaN                None       Q       NaN             NaN                None       M       NaN             NaN                None
3     2015-03-09       YouGov  2015         N/A      A     21.5           26.3             gauche   

In [ ]:
# Création d’un dossier pour stocker les fichiers Excel des élections danoises

output_folder = "election_data"
if not os.path.exists(output_folder):
    os.makedirs(output_folder)                           # Crée le dossier s’il n’existe pas encore

# Définir le pays et le type d'élection

country = "Denmark"
election_type = "general"

# Boucle principale pour traiter chaque année électorale danoise séparément

for year, year_data in wide2_df.groupby('year'):

    # Créer un nom standardisé pour le fichier Excel pour les élections danoises

    file_name = f"{country}_{year}_{election_type}.xlsx"
    file_path = os.path.join(output_folder, file_name)           # Chemin complet du fichier

    # Trie les données par date de sondage

    year_data = year_data.sort_values(by='polling_date')

    # On réorganise les colonnes pour suivre l'ordre demandé et avoir une visualisation plus claire de la situation

    base_columns = ['polling_date', 'sample_size', 'polling_firm']

    # les partis vont être stockés dans cette liste ci-dessous

    party_columns = []
    num_parties = len([col for col in year_data.columns if col.startswith('party')])

    # Boucle pour générer dynamiquement les colonnes de chaque parti

    for i in range(1, num_parties + 1):
        party_columns.extend([f'final_result{i}', f'result{i}', f'party{i}', f'political_leaning{i}'])

    # Combinaison des colonnes dans l’ordre demandé

    ordered_columns = base_columns + party_columns

    # On garde ici uniquement les colonnes qui existent réellement dans le Dataframe crée

    existing_columns = [col for col in ordered_columns if col in year_data.columns]

    # Réorganisation

    year_data = year_data[existing_columns]

    # Sauvegarder en Excel

    year_data.to_excel(file_path, index=False)        # On exclut l'index pour rendre le fichier plus clair

    # Affiche un résumé du téléchargement pour chaque fichier créé

    print(f"Fichier Excel créé: {file_path}")
    print(f"  - Nombre de sondages: {len(year_data)}")
    print(f"  - Période couverte: de {year_data['polling_date'].min()} à {year_data['polling_date'].max()}")


print(f"\nTraitement terminé. {len(wide2_df['year'].unique())} fichiers Excel ont été créés dans le dossier '{output_folder}'.")


Fichier Excel créé: election_data/Denmark_2015_general.xlsx
  - Nombre de sondages: 147
  - Période couverte: de 2015-03-02 à 2015-06-17
Fichier Excel créé: election_data/Denmark_2019_general.xlsx
  - Nombre de sondages: 99
  - Période couverte: de 2019-01-02 à 2019-06-04
Fichier Excel créé: election_data/Denmark_2022_general.xlsx
  - Nombre de sondages: 76
  - Période couverte: de 2022-01-03 à 2022-10-31

Traitement terminé. 3 fichiers Excel ont été créés dans le dossier 'election_data'.


In [ ]:
# STEP 1 : extraction

# Chaque URL correspond à une page Wikipedia avec les données de sondage pour une élection spécifique

urls = [
    "https://en.wikipedia.org/wiki/Opinion_polling_for_the_2002_Czech_parliamentary_election",
    "https://en.wikipedia.org/wiki/Opinion_polling_for_the_2006_Czech_parliamentary_election",
    "https://en.wikipedia.org/wiki/Opinion_polling_for_the_2010_Czech_parliamentary_election",
    "https://en.wikipedia.org/wiki/Opinion_polling_for_the_2013_Czech_parliamentary_election",
    "https://en.wikipedia.org/wiki/Opinion_polling_for_the_2017_Czech_parliamentary_election",
    "https://en.wikipedia.org/wiki/Opinion_polling_for_the_2021_Czech_parliamentary_election"
]

# Dictionnaire des dates exactes des élections parlementaires tchèques

election_dates = {
    "2002": "2002-06-14",  # 14-15 juin 2002
    "2006": "2006-06-02",  # 2-3 juin 2006
    "2010": "2010-05-28",  # 28-29 mai 2010
    "2013": "2013-10-25",  # 25-26 octobre 2013
    "2017": "2017-10-20",  # 20-21 octobre 2017
    "2021": "2021-10-08",  # 8-9 octobre 2021
}

# Associe chaque parti à une orientation politique pour l’analyse

political_leanings = {
    "ČSSD": "gauche", "ODS": "droite", "KSČM": "extrême gauche",
    "KDU-ČSL": "centre droite", "KDU- ČSL": "centre droite", "KDU– ČSL": "centre droite",
    "SZ": "gauche", "US-DEU": "centre", "TOP 09": "centre droite",
    "VV": "centre", "Piráti": "gauche", "ANO": "droite",
    "STAN": "centre", "SPD": "extrême droite", "SPOLU": "centre droite",
}

# Définition d'une fonction pour attribuer un penchant politique à un parti

def get_political_leaning(party_name):

    # Recherche exacte ou partielle du penchant politique

    if party_name in political_leanings:
        return political_leanings[party_name]  # Retourne directement si trouvé

    # Recherche partielle dans le nom du parti
    for known_party, leaning in political_leanings.items():
        if known_party in party_name:
            return leaning                    # Retourne si une correspondance partielle est trouvée

    return "Non catégorisé"                   # Valeur par défaut si rien n’est trouvé

# Définition d'une fonction pour détecter l’année dans une chaîne de date

def detect_year_from_date(date_str, election_year):
    """Comment détecter l'année à partir d'une chaîne de caractère de date"""
                                              # Rechercher directement une année complète (ex. 2002) dans la chaîne
    year_match = re.search(r'\b(20\d{2})\b', date_str)
    if year_match:
        detected_year = int(year_match.group(1))
                                              # Vérifier que l’année est valide (entre 2000 et l’année de l’élection)
        if 2000 <= detected_year <= int(election_year):
            return str(detected_year)

    # On détecte un cas pour 2002 qui nous empêche de référencer dans notre table : le principe ici consiste à gérer les mois de fin d’année (2000 ou 2001)

    if election_year == "2002":
        months_prev_years = ["oct", "nov", "dec", "september", "october", "november", "december"]
        for month in months_prev_years:
            if month.lower() in date_str.lower():
                                              # Attribution de 2000 ou 2001 si cela est mentionné
                if "2000" in date_str:
                    return "2000"
                elif "2001" in date_str:
                    return "2001"
                                              # Sinon attribution par défaut à l'année précédente
                return str(int(election_year) - 1)

                                              # Utilisation par défaut de l’année de l’élection
    return election_year

# Fonction pour la standardisation des dates

def standardize_date(date_str, year):
    """Standardisation du format des dates"""
                                              # Vérifier si la date est vide ou non pertinente
    if not date_str or date_str.strip() in ["N/A", "–", "—"]:
        return None

    try:

        # Détecter l’année dans la chaîne

        detected_year = detect_year_from_date(date_str, year)
        year_to_use = detected_year

        # Dictionnaire pour convertir les noms de mois en nombres

        months = {
            'jan': '01', 'feb': '02', 'mar': '03', 'apr': '04', 'may': '05', 'jun': '06',
            'jul': '07', 'aug': '08', 'sep': '09', 'oct': '10', 'nov': '11', 'dec': '12',
            'january': '01', 'february': '02', 'march': '03', 'april': '04', 'june': '06',
            'july': '07', 'august': '08', 'september': '09', 'october': '10', 'november': '11', 'december': '12'
        }

        # Convertion des mois écrits en chiffres

        date_lower = date_str.lower()
        for month_name, month_num in months.items():
            date_lower = re.sub(fr'\b{month_name}\b', month_num, date_lower)

        # Si la date est une plage de date on en prend la dernière

        if any(sep in date_lower for sep in ["–", "-", "—"]):
            date_parts = re.split(r'[–\-—]', date_lower)
            date_lower = date_parts[-1].strip()

        # Extraction des jours et des mois

        month_day_match = re.search(r'(\d{1,2})[.\s/]*(\d{1,2})', date_lower)
        if month_day_match:
            day, month = month_day_match.groups()
            day = day.zfill(2)                     # Permet d'ajouter un 0 en préfixe à celui existant
            month = month.zfill(2)
            return f"{year_to_use}-{month}-{day}"  # Convertion des dates existantes en année-mois-jour

        # Si on trouve que le mois, on lui attribue le 1er jour du mois

        for month_name, month_num in months.items():
            if month_name in date_lower:
                return f"{year_to_use}-{month_num}-01"

        # De même si le mois n'est pas trouvé, on lui attribue le 1er jour du mois de janvier

        return f"{year_to_use}-01-01"

    except:
        return f"{year}-01-01"                    # En cas d’erreur, là aussi on lui attribue le 1er janvier

# Définition d'une fonction pour nettoyer les valeurs de résultats

def clean_result_value(result_str):
    """Nettoie les valeurs des résultats"""
                                                  # Vérification si la valeur est vide ou non pertinente
    if not result_str or result_str.strip() in ["–", "—", "N/A", "-"]:
        return None

    # Supprimer tout sauf les chiffres et le point décimal

    cleaned = re.sub(r'[^0-9.]', '', result_str)
    if not cleaned:
        return None                              # Si c'est impossible, retourne None

    try:
        return float(cleaned)                    # Sinon on peut transformer en nombre décimal
    except:
        return None

# Fonction pour savoir et vérifier si une chaîne ressemble à un résultat de sondage

def is_likely_result(text):
    """Vérifie si une chaîne s'apparente à un résultat de sondage"""
    cleaned = re.sub(r'[^0-9.]', '', text)
    if not re.search(r'\d', cleaned):
        return False

    try:
        value = float(cleaned)
        return 0 <= value <= 100                 # Vérifier si le pourcentage associé est valide
    except:
        return False

# Fonction pour identifier les types de colonnes dans les en-têtes

def identify_column_types(headers):
    """Identifie les colonnes : institut de sondage, date et taille d'échantillon"""
    polling_keywords = ['poll', 'polling', 'pollster', 'firm', 'agency', 'institute', 'company']
    date_keywords = ['date', 'field', 'fieldwork', 'conducted', 'period']
    sample_keywords = ['sample', 'size', 'respondents', 'participants']

    polling_idx, date_idx, sample_idx = None, None, None

    # Utilisation d'une boucle pour parcourir chaque en-tête et identifier les colonnes

    for i, header in enumerate(headers):
        h_lower = header.lower()

        # Colonne sondage

        if any(kw in h_lower for kw in polling_keywords) and 'date' not in h_lower and 'sample' not in h_lower:
            polling_idx = i

        # Colonne date

        elif any(kw in h_lower for kw in date_keywords):
            date_idx = i

        # Taille échantillon

        elif any(kw in h_lower for kw in sample_keywords):
            sample_idx = i

    # Si des colonnes ne sont pas trouvées on leur attribut des valeurs

    if polling_idx is None and date_idx is None:
        polling_idx, date_idx = 0, 1                           # Les deux premières sont institut de sondage et date
    elif polling_idx is None:
        polling_idx = max(0, date_idx - 1) if date_idx > 0 else date_idx + 1
    elif date_idx is None:
        date_idx = polling_idx + 1 if polling_idx < len(headers) - 1 else polling_idx - 1

    return polling_idx, date_idx, sample_idx

# Fonction pour extraire la taille d’échantillon

def extract_sample_size(text):
    """Extrait la taille d'échantillon à partir d'une chaîne de texte"""
                                                              # Modèles pour reconnaître les tailles d’échantillon (ex. "n = 1234")
    patterns = [
        r'n\s*=\s*(\d[\d,.]*)',                       # n = 1234
        r'N\s*=\s*(\d[\d,.]*)',                       # N = 1234
        r'sample\s*[:-]?\s*(\d[\d,.]*)',              # sample: 1234
        r'(\d[\d,.]*)\s*respondents',                 # 1234 respondents
        r'(\d[\d,.]*)(?:\s*people|\s*participants)',  # 1234 people/participants
    ]

    # On peut enfin utiliser une Boucle pour tester chaque modèle

    for pattern in patterns:
        match = re.search(pattern, text, re.IGNORECASE)
        if match:
                                                              # Nettoyage et convertion en nombre réels
            sample_str = match.group(1).replace(',', '').replace('.', '')
            try:
                return int(sample_str)
            except:
                pass

    # Ici, si le nombre est brut on le considère quand même comme un nombre

    if re.match(r'^\d[\d,.]*$', text.strip()):
        try:
            return int(text.replace(',', '').replace('.', ''))
        except:
            pass

    return None

# Fonction pour vérifier si une chaîne est une taille d’échantillon

def is_sample_size(text):
    """Vérifie si une chaîne est une taille d'échantillon"""
                                                  # Est ce que le texte peut etre lu sous forme numérique
    if re.match(r'^\d[\d,.]*$', text.strip()):
        return True

    # Vérifier les modèles courants de taille d’échantillon

    sample_patterns = [
        r'n\s*=\s*\d',
        r'N\s*=\s*\d',
        r'sample\s*[:-]?\s*\d',
        r'\d+\s*respondents',
        r'\d+\s*people',
        r'\d+\s*participants',
    ]

    # Nouvelle boucle pour vérifier chaque modèle avec l'ajouts des modèles courants

    for pattern in sample_patterns:
        if re.search(pattern, text, re.IGNORECASE):
            return True

    return False

# Fonction pour vérifier et corriger le contenu des colonnes

def verify_column_content(row, polling_firm_idx, poll_date_idx, sample_idx, year):
    """Vérification si le contenu des colonnes est identifié et extrait par même les données"""
    col1 = row[polling_firm_idx].get_text(strip=True) if polling_firm_idx < len(row) else ""
    col2 = row[poll_date_idx].get_text(strip=True) if poll_date_idx < len(row) else ""

    # Premièrement on extraie la taille de l'échantillon

    sample_size = None
    if sample_idx is not None and sample_idx < len(row):
        sample_text = row[sample_idx].get_text(strip=True)
        sample_size = extract_sample_size(sample_text)

    # Ensuite on peut vérifier si la colonne 1 est une taille d'échantillon

    if is_sample_size(col1) and not is_sample_size(col2):
        sample_size = extract_sample_size(col1)

        # Chercher l’institut de sondage stocké dans une autre colonne

        for i, cell in enumerate(row):
            if i != polling_firm_idx and i != poll_date_idx and i != sample_idx:
                cell_text = cell.get_text(strip=True)
                if not is_likely_result(cell_text) and not is_sample_size(cell_text):
                    col1 = cell_text
                    break

    # Expressions pour détecter les dates

    date_patterns = [
        r'\d{1,2}[-–]\d{1,2}\s+\w+',
        r'\d{1,2}\s+\w+[-–]\d{1,2}\s+\w+',
        r'\w+\s+\d{1,2}[-–]\d{1,2}',
        r'\d{1,2}[./]\d{1,2}',
        r'\d{4}-\d{2}-\d{2}',
        r'[A-Za-z]+\s+\d{4}',
        r'\d{4}'
    ]

    # Compter les correspondances de date dans chaque colonne

    col1_date_matches = sum(1 for pattern in date_patterns if re.search(pattern, col1, re.IGNORECASE))
    col2_date_matches = sum(1 for pattern in date_patterns if re.search(pattern, col2, re.IGNORECASE))

    # Si la colonne 1 s'apparente à des dates on l'inverse avec

    if col1_date_matches > col2_date_matches:
        return col2, col1, sample_size

    return col1, col2, sample_size

# Fonction pour détecter si une ligne est un résultat d’élection

def is_election_result(polling_firm):
    """Association de l'institut de sondage à la date du sondage"""
    election_keywords = [
        'election', 'result', 'legislative', 'parliament', 'official',
        'electoral', 'final', 'outcome', 'actual', 'elected'
    ]

    polling_firm_lower = polling_firm.lower()
    return any(keyword in polling_firm_lower for keyword in election_keywords)

# Fonction pour valider un nom d’institut de sondage

def is_valid_polling_firm(text):
    """Vérifie si le texte est un nom d'institut de sondage valide"""
    if not text or len(text) < 2:
        return False

    if re.match(r'^[\d,.\s]+$', text):        # Rejette les nombres seuls
        return False

    if "%" in text:                           # Rejette les pourcentages
        return False

    if re.match(r'^\d+\s*[a-zA-Z]+$', text):  # Rejette "123 abc"
        return False

    return True

# Fonction pour vérifier si une date est proche de l’élection

def is_date_close_to_election(date_str, year):
    """Vérifie si une date est proche de la date d'élection correspondante"""
    if year not in election_dates:
        return False

    try:
        poll_date = pd.to_datetime(date_str)
        election_date = pd.to_datetime(election_dates[year])
        date_diff = abs((poll_date - election_date).days)
        return date_diff <= 7                                 # On laisse une marge de 7 jours entre le sondage et l'élection
    except:
        return False

# Fonction pour extraire les résultats officiels des élections

def extract_final_results(all_polls):
    """Extrait les résultats officiels des élections à partir des données de sondage"""
    final_results = {}

    # Groupement des sondages par année

    years = sorted(all_polls['year'].unique())

    # Boucle sur chaque année

    for year in years:
        year_str = str(int(year))
        year_polls = all_polls[all_polls['year'] == year]

        # Filtrage des résultats d’élection avec deux critères

        election_polls = year_polls[
            (year_polls['polling_firm'].apply(is_election_result)) &
            (year_polls['polling_date'].apply(lambda x: is_date_close_to_election(x, year_str)))
        ]

        # Si vide, essayer uniquement avec le nom pour retrouver la date

        if election_polls.empty:
            election_polls = year_polls[year_polls['polling_firm'].apply(is_election_result)]

            # On réessaye et si c'est toujours vide, on cherche les sondages proches de l’élection

            if election_polls.empty and year_str in election_dates:
                election_date = pd.to_datetime(election_dates[year_str])
                if not year_polls.empty:
                    year_polls['date_diff'] = abs((year_polls['polling_date'] - election_date).dt.days)
                    closest_polls = year_polls.nsmallest(3, 'date_diff')
                    election_polls = closest_polls[closest_polls['date_diff'] <= 14]

        if not election_polls.empty:
            year_results = {}

            # Boucle sur les lignes pour extraire les résultats

            for _, row in election_polls.iterrows():
                party = row['political_party']
                result = row['result']
                if party not in year_results and result is not None:
                    year_results[party] = result

            if year_results:
                final_results[year_str] = year_results

    return final_results

# Fonction principale pour scraper les données

def scrape_czech_polls():
    all_polls_data = []      # Liste pour les données au format long
    final_polls = []         # Liste pour les sondages complets
    party_names_global = []  # Liste des noms de partis uniques

    # Boucle sur chaque URL

    for url in urls:

        # Extraire l’année de l’URL

        match = re.search(r'(\d{4})_Czech', url)
        if not match:
            continue
        year = match.group(1)

        # Récupérer et parser la page

        response = requests.get(url)
        soup = BeautifulSoup(response.text, 'html.parser')

        # Trouver le premier tableau de la page Wikipédia

        table = soup.find('table', class_='wikitable')
        if not table:
            continue

        # Extraire les en-têtes

        headers = []
        header_row = table.find('tr')
        if header_row:
            headers = [header.get_text(strip=True) for header in header_row.find_all(['th', 'td'])]

        # Identifier les colonnes clés définies ci-dessous

        polling_firm_idx, poll_date_idx, sample_idx = identify_column_types(headers)

        # Identification des colonnes des partis

        party_indices = []
        party_names = []
        for i, header in enumerate(headers):
            header_lower = header.lower()
            if i != polling_firm_idx and i != poll_date_idx and i != sample_idx and i > 1:
                if "%" not in header_lower and "lead" not in header_lower and "sample" not in header_lower:
                    party_indices.append(i)
                    party_names.append(header)
                    if header not in party_names_global:
                        party_names_global.append(header)

        # Boucle sur les lignes du tableau

        for row in table.find_all('tr')[1:]:                                      # Ignore l’en-tête
            cols = row.find_all(['td', 'th'])
            if len(cols) >= 3:
                try:
                    polling_firm, poll_date_text, sample_size = verify_column_content(
                        cols, polling_firm_idx, poll_date_idx, sample_idx, year   # Vérifier et extraire les données des colonnes
                    )

                    # Chercher la taille d’échantillon dans d’autres colonnes si absente

                    if sample_size is None:
                        for cell in cols:
                            cell_text = cell.get_text(strip=True)
                            if is_sample_size(cell_text):
                                extracted_size = extract_sample_size(cell_text)
                                if extracted_size and 500 <= extracted_size <= 20000:
                                    sample_size = extracted_size
                                    break

                    # Ignorer les lignes invalides toujours invalides

                    if not poll_date_text or not polling_firm or not is_valid_polling_firm(polling_firm):
                        continue

                    # Standardiser la date

                    polling_date = standardize_date(poll_date_text, year)
                    if not polling_date:
                        continue

                    # Vérifier si c’est un résultat d’élection et pas autre chose

                    is_election = is_election_result(polling_firm)
                    is_real_election = is_election and is_date_close_to_election(polling_date, year)

                    # Créer un id unique pour le sondage

                    poll_id = f"{year}_{polling_firm}_{polling_date}".replace(" ", "_").replace("/", "-")
                    poll_results = {}

                    # Boucle pour collecter les résultats des partis

                    for i, party_idx in enumerate(party_indices):
                        if party_idx < len(cols):
                            party_name = party_names[i]
                            party_result_text = cols[party_idx].get_text(strip=True)
                            party_result = clean_result_value(party_result_text)
                            if party_result is not None:
                                poll_results[party_name] = party_result

                    # Ajouter les données au format long de défaut

                    for party_name, result in poll_results.items():
                        poll_data = {
                            'year': year,
                            'polling_firm': polling_firm,
                            'polling_date': polling_date,
                            'political_party': party_name,
                            'political_leaning': get_political_leaning(party_name),
                            'result': result,
                            'is_election_result': is_election,
                            'is_real_election': is_real_election,
                            'sample_size': sample_size
                        }
                        all_polls_data.append(poll_data)

                    # Ajouter le sondage complet

                    if poll_results:
                        final_poll = {
                            'poll_id': poll_id,
                            'year': year,
                            'polling_firm': polling_firm,
                            'polling_date': polling_date,
                            'results': poll_results,
                            'is_election_result': is_election,
                            'is_real_election': is_real_election,
                            'sample_size': sample_size
                        }
                        final_polls.append(final_poll)

                except Exception as e:
                    continue

    # Créer un DataFrame avec les données collectées et partiellement traitées

    df = pd.DataFrame(all_polls_data)

    # Nettoyer et convertir les dates

    if not df.empty and 'polling_date' in df.columns:
        df['polling_date'] = pd.to_datetime(df['polling_date'], errors='coerce')
        df = df.dropna(subset=['polling_date'])

    # Convertir et trier par année

    if not df.empty and 'year' in df.columns:
        df['year'] = pd.to_numeric(df['year'], errors='coerce')
        df = df.dropna(subset=['year'])
        df['year'] = df['year'].astype(int)
        df = df.sort_values(by=['year', 'polling_date'])

    # Extraire les résultats finaux

    final_results = extract_final_results(df)

    # Ajouter la colonne des résultats finaux qui peut mainteannt être faite

    if not df.empty:
        df['final_result'] = None
        for idx, row in df.iterrows():
            year_str = str(int(row['year']))
            party = row['political_party']
            if year_str in final_results and party in final_results[year_str]:
                df.at[idx, 'final_result'] = final_results[year_str][party]

    return df, final_polls, party_names_global, final_results

# Exécuter le script

czech_polls_df, final_polls, party_names_global, final_results = scrape_czech_polls()

# Configurer pandas pour un affichage complet et sans bavures

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.width', 1000)
pd.set_option('display.expand_frame_repr', False)
pd.set_option('display.max_colwidth', None)

# Supprimer certaines colonnes entachant la table finale

czech_polls_df = czech_polls_df.drop(columns=['is_election_result'])
if 'is_real_election' in czech_polls_df.columns:
    czech_polls_df = czech_polls_df.drop(columns=['is_real_election'])

czech_polls_df

year                 polling_firm polling_date political_party political_leaning   result  sample_size final_result
120   2002             Sofres-Factum[6]   2000-01-09            ČSSD            gauche  11.2000          NaN         30.2
121   2002             Sofres-Factum[6]   2000-01-09             ODS            droite  20.1000          NaN         24.5
122   2002             Sofres-Factum[6]   2000-01-09              4K    Non catégorisé  21.3000          NaN         14.3
123   2002             Sofres-Factum[6]   2000-01-09            KSČM    extrême gauche  15.9000          NaN         18.5
115   2002                      STEM[5]   2001-01-20            ČSSD            gauche  17.6000          NaN         30.2
116   2002                      STEM[5]   2001-01-20             ODS            droite  16.0000          NaN         24.5
117   2002                      STEM[5]   2001-01-20              4K    Non catégorisé  15.7000          NaN         14.3
118   2002                      STEM[5]   2001-01-20            KSČM    extrême gauche  15.7000          NaN         18.5
119   2002                      STEM[5]   2001-01-20          Others    Non catégorisé  19.8000          NaN         12.5
110   2002                      STEM[4]   2001-02-20            ČSSD            gauche  17.7000          NaN         30.2
111   2002                      STEM[4]   2001-02-20             ODS            droite  18.0000          NaN         24.5
112   2002                      STEM[4]   2001-02-20              4K    Non catégorisé  29.7000          NaN         14.3
113   2002                      STEM[4]   2001-02-20            KSČM    extrême gauche  16.2000          NaN         18.5
114   2002                      STEM[4]   2001-02-20          Others    Non catégorisé  18.4000          NaN         12.5
105   2002                         STEM   2001-03-20            ČSSD            gauche  16.3000          NaN         30.2
106   2002                         STEM   2001-03-20             ODS            droite  19.7000          NaN         24.5
107   2002                         STEM   2001-03-20              4K    Non catégorisé  29.8000          NaN         14.3
108   2002                         STEM   2001-03-20            KSČM    extrême gauche  17.1000          NaN         18.5
109   2002                         STEM   2001-03-20          Others    Non catégorisé  17.1000          NaN         12.5
100   2002                         STEM   2001-04-20            ČSSD            gauche  20.4000          NaN         30.2
101   2002                         STEM   2001-04-20             ODS            droite  20.8000          NaN         24.5
102   2002                         STEM   2001-04-20              4K    Non catégorisé  25.5000          NaN         14.3
103   2002                         STEM   2001-04-20            KSČM    extrême gauche  14.1000          NaN         18.5
104   2002                         STEM   2001-04-20          Others    Non catégorisé  19.2000          NaN         12.5
95    2002                         STEM   2001-05-20            ČSSD            gauche  20.7000          NaN         30.2
96    2002                         STEM   2001-05-20             ODS            droite  22.0000          NaN         24.5
97    2002                         STEM   2001-05-20              4K    Non catégorisé  25.7000          NaN         14.3
98    2002                         STEM   2001-05-20            KSČM    extrême gauche  16.7000          NaN         18.5
99    2002                         STEM   2001-05-20          Others    Non catégorisé  14.6000          NaN         12.5
90    2002                         STEM   2001-06-20            ČSSD            gauche  19.2000          NaN         30.2
91    2002                         STEM   2001-06-20             ODS            droite  22.4000          NaN         24.5
92    2002                         STEM   2001-06-20              4K    Non catégorisé  23.5000       

In [ ]:
# STEP 2 : CLEANING

# Ce DataFrame contient les données brutes des sondages tchèques au format long

# Dictionnaire pour uniformiser les noms des partis, y compris les variantes de Others

party_name_mapping = {
    'ČSSD': 'ČSSD', 'CSSD': 'ČSSD', 'SOCDEM': 'ČSSD',
    'ODS': 'ODS',
    'KSČM': 'KSČM',
    'KDU-ČSL': 'KDU-ČSL', 'KDU–ČSL': 'KDU-ČSL', 'KDU- ČSL': 'KDU-ČSL', 'KDU CSL': 'KDU-ČSL',
    'SZ': 'SZ', 'Zelení': 'SZ', 'Greens': 'SZ',
    'US-DEU': 'US-DEU', 'US–DEU': 'US-DEU',
    'TOP 09': 'TOP 09', 'TOP09': 'TOP 09',
    'VV': 'VV',
    'Piráti': 'Piráti', 'Pirates': 'Piráti', 'Czech Pirate Party': 'Piráti',
    'ANO': 'ANO', 'ANO 2011': 'ANO',
    'STAN': 'STAN',
    'SPD': 'SPD',
    'SPOLU': 'SPOLU',
    'Others': 'Others', 'Oth.': 'Others', 'Oth': 'Others', 'Jiní': 'Others', 'Other': 'Others',
    'others': 'Others',
    'other': 'Others'
}

# La première étape consiste à appliquer le mapping pour uniformiser les noms des partis dans le DataFrame

czech_polls_df['political_party'] = czech_polls_df['political_party'].replace(party_name_mapping)

# La deuxième étape consiste à filtrer pour ne garder que les sondages tout en excluant les résultats d’élection officiels

keywords_to_remove = ['election', 'legislative', 'turnout', 'vote', 'ballot', 'result', 'official', 'final']
czech_polls_df_filtered = czech_polls_df[
    ~czech_polls_df['polling_firm'].str.lower().str.contains('|'.join(keywords_to_remove), na=False)
]

# "Others" est conservé car il peut apparaître dans les sondages, pas seulement les résultats officiels

# L'étape 3 est d'xtraire la liste des partis uniques après filtrage, pour préparer la transformation en format "wide"

unique_parties = czech_polls_df_filtered['political_party'].unique()

# Cette liste inclut "Others" car il est traité comme un parti à part entière

# Etape 4 : Transformation des données "long" (une ligne par parti) en wide soit une ligne par sondages

wide_data = []                                          # Liste pour stocker les données transformées
grouped = czech_polls_df_filtered.groupby(['polling_date', 'polling_firm', 'year', 'sample_size'], dropna=False)

# Regroupement par sondage (date, firme, année, taille d’échantillon) pour traiter chaque sondage séparément

# Boucle principale consistant à parcourir maintenant chaque groupe

for group_key, group in grouped:
    polling_date, polling_firm, year, sample_size = group_key  # Décomposer les clés du groupe
                                                               # Créer un dictionnaire avec les données communes à tous les partis pour ce sondage
    common_data = {
        'polling_date': polling_date,
        'polling_firm': polling_firm,
        'year': year,
        'sample_size': sample_size
    }

    # nouveau dictionnaire pour stocker les résultats de chaque parti dans ce sondage

    party_results = {}

    # Boucle de boucle : parcourir chaque ligne du groupe (chaque parti dans le sondage)

    for _, row in group.iterrows():
        party = row['political_party']
                                                               # Condition nécessaire pour éviter les doublons et privilégier les valeurs non nulles
        if party not in party_results or (party_results[party]['result'] is None and row['result'] is not None):
            party_results[party] = {
                'result': row['result'],                       # Résultat du sondage
                'final_result': row['final_result'],           # Résultat officiel (si disponible)
                'political_leaning': row['political_leaning']  # Orientation politique
            }

    # Boucle de formatage qui ajoute les données de chaque partis

    for i, party in enumerate(unique_parties, start=1):
        if party in party_results:
                                                 # Si le parti est présent dans ce sondage, ajouter ses données
            common_data[f'party{i}'] = party
            common_data[f'result{i}'] = party_results[party]['result']
            common_data[f'final_result{i}'] = party_results[party]['final_result']
            common_data[f'political_leaning{i}'] = party_results[party]['political_leaning']
        else:
                                                 # Si le parti n’est pas dans ce sondage, autrement on comble avec None
            common_data[f'party{i}'] = party
            common_data[f'result{i}'] = None
            common_data[f'final_result{i}'] = None
            common_data[f'political_leaning{i}'] = None

    wide_data.append(common_data)

# Et dernière étape qui est de convertir la liste de tous les dictionnaires en un DataFrame

wide_df = pd.DataFrame(wide_data)

# Et pour cloturer on trie le DataFrame par année et date de sondage pour une lecture chronologique et plus lisible

wide_df = wide_df.sort_values(by=['year', 'polling_date'])

# Identifier les colonnes des partis pour vérifier la présence de "Others"

party_columns = [col for col in wide_df.columns if col.startswith('party')]
others_rows = wide_df[wide_df[party_columns].eq('Others').any(axis=1)]

wide_df

polling_date        polling_firm  year  sample_size party1  result1  final_result1 political_leaning1 party2  result2  final_result2 political_leaning2 party3  result3  final_result3 political_leaning3 party4  result4  final_result4 political_leaning4  party5  result5  final_result5 political_leaning5   party6  result6  final_result6 political_leaning6 party7  result7  final_result7 political_leaning7  party8  result8  final_result8 political_leaning8 party9  result9  final_result9 political_leaning9 party10  result10  final_result10 political_leaning10 party11  result11  final_result11 political_leaning11 party12  result12  final_result12 political_leaning12 party13  result13  final_result13 political_leaning13 party14  result14  final_result14 political_leaning14     party15  result15  final_result15 political_leaning15    party16  result16  final_result16 political_leaning16 party17  result17  final_result17 political_leaning17 party18  result18  final_result18 political_leaning18 party19  result19  final_result19 political_leaning19 party20  result20  final_result20 political_leaning20 party21  result21  final_result21 political_leaning21  party22  result22  final_result22 political_leaning22 party23  result23  final_result23 political_leaning23 party24  result24 final_result24 political_leaning24 party25  result25  final_result25 political_leaning25   party26  result26  final_result26 political_leaning26 party27  result27  final_result27 political_leaning27 party28  result28 final_result28 political_leaning28 party29  result29  final_result29 political_leaning29      party30  result30  final_result30 political_leaning30   party31  result31  final_result31 political_leaning31 party32  result32  final_result32 political_leaning32 party33  result33  final_result33 political_leaning33 party34  result34  final_result34 political_leaning34         party35  result35  final_result35 political_leaning35 party36  result36  final_result36 political_leaning36  party37  result37 final_result37 political_leaning37 party38  result38  final_result38 political_leaning38
0     2000-01-09    Sofres-Factum[6]  2002          NaN   ČSSD  11.2000          30.20             gauche    ODS  20.1000         24.500             droite     4K     21.3           14.3     Non catégorisé   KSČM  15.9000         18.500     extrême gauche  Others      NaN            NaN               None  KDU-ČSL      NaN            NaN               None     SZ      NaN            NaN               None  US-DEU      NaN            NaN               None    NEZ      NaN            NaN               None  SNK-ED       NaN             NaN                None  NEZDEM       NaN             NaN                None  TOP 09       NaN             NaN                None      VV       NaN             NaN                None     SPO       NaN             NaN                None  TOP 09STAN       NaN             NaN                None  ÚSVIT(VV)       NaN             NaN                None  KDUČSL       NaN             NaN                None    SPOZ       NaN             NaN                None    DSSS       NaN             NaN                None  PIRÁTI       NaN             NaN                None     ANO       NaN             NaN                None  turnout       NaN             NaN                None      HV       NaN             NaN                None    STAN       NaN           None                None  ZELENÍ       NaN             NaN                None  SVOBODNÍ       NaN             NaN                None     SPD       NaN             NaN                None    REAL       NaN           None                None   SPOLU       NaN             NaN                None  Piráti+STAN       NaN             NaN                None  T–S–SsČR       NaN             NaN                None       Z       NaN             NaN                None      VB       NaN             NaN                None     PSH       NaN             NaN                None  Govt.+ sup.[a]       NaN     

In [ ]:
# STEP 3 : convertion au format excel

# Création d’un dossier pour stocker les fichiers Excel générés

output_folder = "election_data"
if not os.path.exists(output_folder):
    os.makedirs(output_folder)  # Création du dossier s’il n’existe pas déjà

# Définir le pays et le type d'élection

country = "Czech"
election_type = "parliamentary"

# Boucle principale pour traiter chaque année séparément

for year, year_data in wide_df.groupby('year'):

    # Créer un nom standardisé pour le fichier Excel des élections tchèques

    file_name = f"{country}_{year}_{election_type}.xlsx"
    file_path = os.path.join(output_folder, file_name)              # Chemin complet du fichier

    # Trier les données par date de sondage par ordre chronologique défini avant

    year_data = year_data.sort_values(by='polling_date')

    # Réorganiser les colonnes pour suivre l’ordre demandé

    base_columns = ['polling_date', 'sample_size', 'polling_firm']

    # Organisation des colonnes dans l'ordre demandé

    party_columns = []                                               # Liste pour stocker les colonnes des partis
    num_parties = len([col for col in year_data.columns if col.startswith('party')])  # Nombre de partis uniques

    # Boucle pour générer dynamiquement les colonnes de chaque parti

    for i in range(1, num_parties + 1):
        party_columns.extend([f'final_result{i}', f'result{i}', f'party{i}', f'political_leaning{i}'])

    # On combine cette fois ci les colonnes dans l’ordre demandé

    ordered_columns = base_columns + party_columns

    # Filtrer pour inclure uniquement les colonnes qui existent réellement dans le DataFrame et évite les erreurs si certaines colonnes sont absentes

    existing_columns = [col for col in ordered_columns if col in year_data.columns]

    # Réorganiser le DataFrame

    year_data = year_data[existing_columns]

    # Sauvegarder en Excel

    year_data.to_excel(file_path, index=False)          # Exporte sans l’index pour un fichier propre

    # Afficher un résumé pour chaque fichier créé et voir si ça convertion est éffectuée

    print(f"Nom du fichier excel crée : {file_path}")
    print(f"  - Nombre de sondages contenus dans le fichier : {len(year_data)}")  # Nombre de lignes (sondages) dans le fichier
    print(f"  - Période couverte dans le fichier : de {year_data['polling_date'].min()} à {year_data['polling_date'].max()}")

print(f"\nExecution et enregistrement des fichiers terminés. {len(wide_df['year'].unique())} les fichiers ont été déposé dans le dossier '{output_folder}'.")


Fichier Excel créé: election_data/Czech_2002_parliamentary.xlsx
  - Nombre de sondages: 23
  - Période couverte: de 2000-01-09 00:00:00 à 2002-06-12 00:00:00
Fichier Excel créé: election_data/Czech_2006_parliamentary.xlsx
  - Nombre de sondages: 74
  - Période couverte: de 2002-10-10 00:00:00 à 2006-05-26 00:00:00
Fichier Excel créé: election_data/Czech_2010_parliamentary.xlsx
  - Nombre de sondages: 50
  - Période couverte: de 2008-01-16 00:00:00 à 2010-05-12 00:00:00
Fichier Excel créé: election_data/Czech_2013_parliamentary.xlsx
  - Nombre de sondages: 10
  - Période couverte: de 2013-02-22 00:00:00 à 2013-09-25 00:00:00
Fichier Excel créé: election_data/Czech_2017_parliamentary.xlsx
  - Nombre de sondages: 7
  - Période couverte: de 2017-09-01 00:00:00 à 2017-10-16 00:00:00
Fichier Excel créé: election_data/Czech_2021_parliamentary.xlsx
  - Nombre de sondages: 55
  - Période couverte: de 2021-01-01 00:00:00 à 2021-09-30 00:00:00

Traitement terminé. 6 fichiers Excel ont été créés d

In [ ]:
# Définition de la classe pour l’interface interactive
class ElectionPollingCLI:
    def __init__(self, wide_df, wide2_df):
        # Initialisation avec les deux ensembles de données au format "wide"
        self.datasets = {
            'Czech Republic': wide_df,  # Données tchèques du script précédent
            'Denmark': wide2_df         # Données danoises du script précédent
        }
        self.selected_dataset = None  # Dataset actuellement sélectionné
        self.selected_country = None  # Pays actuellement sélectionné
        self.select_dataset()  # Lancer la sélection initiale du dataset

    def select_dataset(self):
        """Initial dataset selection"""
        # Méthode pour choisir entre les datasets tchèque et danois
        while True:  # Boucle infinie jusqu’à un choix valide ou sortie
            print("\n--- Select Dataset ---")
            # Afficher les options disponibles
            for i, (country, df) in enumerate(self.datasets.items(), 1):
                print(f"{i}. {country}")
            print("4. Exit")

            try:
                choice = input("\nSelect a dataset (1-4): ")

                if choice == '1':
                    self.selected_dataset = self.datasets['Czech Republic']
                    self.selected_country = 'Czech Republic'
                    self.main_menu()  # Passer au menu principal
                    break
                elif choice == '2':
                    self.selected_dataset = self.datasets['Denmark']
                    self.selected_country = 'Denmark'
                    self.main_menu()  # Passer au menu principal
                    break
                elif choice == '4':
                    print("Exiting dashboard. Goodbye!")
                    break  # Quitter l’interface
                else:
                    print("Invalid option. Please try again.")
            except Exception as e:
                print(f"An error occurred: {e}")

    def view_polling_trends(self):
        """
        Visualize polling trends with interactive party selection and enhanced visualization
        """
        # Méthode pour visualiser les tendances des sondages pour un parti sélectionné
        plt.style.use('ggplot')  # Appliquer un style graphique prédéfini

        # Identifier les colonnes des partis et des résultats
        party_columns = [col for col in self.selected_dataset.columns if col.startswith('party')]
        result_columns = [col for col in self.selected_dataset.columns if col.startswith('result') and not col.startswith('final_result')]

        # Extraire les noms de partis uniques
        parties = []
        for col in party_columns:
            parties.extend(self.selected_dataset[col].dropna().unique())
        parties = list(dict.fromkeys(parties))  # Supprimer les doublons tout en préservant l’ordre

        if not parties:
            print("No parties found in the dataset.")
            return

        # Afficher les partis disponibles
        print("\nAvailable Parties:")
        for i, party in enumerate(parties, 1):
            print(f"{i}. {party}")

        # Sélection interactive du parti
        while True:  # Boucle jusqu’à une entrée valide
            try:
                party_choice = int(input("\nSelect a party (number): ")) - 1
                selected_party = parties[party_choice]
                break
            except (ValueError, IndexError):
                print("Invalid selection. Try again.")

        # Trouver la colonne de résultat correspondante
        result_col = None
        for i in range(1, len(result_columns) + 1):  # Boucle sur les indices des colonnes
            party_col = f'party{i}'
            mask = self.selected_dataset[party_col] == selected_party
            if mask.any():
                result_col = f'result{i}'
                break

        if not result_col:
            print(f"Unable to find data for {selected_party}")
            return

        # Assurer que la colonne 'year' est numérique
        self.selected_dataset['year'] = pd.to_numeric(self.selected_dataset['year'], errors='coerce')

        # Grouper les données par année pour calculer la moyenne
        grouped_data = self.selected_dataset.groupby('year')[result_col].mean().reset_index()

        # Créer une visualisation améliorée
        plt.figure(figsize=(15, 8))  # Taille de la figure
        plt.plot(grouped_data['year'], grouped_data[result_col],
                 marker='o', linestyle='-', linewidth=2,
                 color='#1E90FF', markersize=8,
                 label=f'{selected_party} Trend')  # Ligne de tendance

        # Ajouter un intervalle de confiance
        std_dev = grouped_data[result_col].std()
        plt.fill_between(grouped_data['year'],
                         grouped_data[result_col] - std_dev,
                         grouped_data[result_col] + std_dev,
                         color='lightblue', alpha=0.3)

        # Mise en forme
        plt.title(f"Polling Trends for {selected_party} ({self.selected_country})",
                  fontsize=16, fontweight='bold')
        plt.xlabel("Year", fontsize=12)
        plt.ylabel("Average Results (%)", fontsize=12)
        plt.gca().xaxis.set_major_locator(plt.MaxNLocator(integer=True))  # Années entières
        plt.grid(True, linestyle='--', linewidth=0.5, color='lightgray')
        plt.legend()
        plt.tight_layout()

        # Annotations statistiques
        mean_val = grouped_data[result_col].mean()
        max_val = grouped_data[result_col].max()
        min_val = grouped_data[result_col].min()
        stats_text = (f"Mean: {mean_val:.2f}%\n"
                      f"Maximum: {max_val:.2f}%\n"
                      f"Minimum: {min_val:.2f}%")
        plt.annotate(stats_text, xy=(0.02, 0.95), xycoords='axes fraction',
                     verticalalignment='top', bbox=dict(boxstyle='round', facecolor='white', alpha=0.7))

        # Afficher le graphique
        plt.show()

        # Option pour voir les données détaillées
        show_data = input("Would you like to see detailed data? (yes/no): ").lower()
        if show_data in ['yes', 'y', 'oui', 'o']:
            print("\nDetailed Data:")
            print(grouped_data.to_string(index=False))

    def calculate_summary_statistics(self):
        """
        Calculate and display summary statistics for selected dataset with year selection
        """
        # Méthode pour calculer et afficher des statistiques par parti et année
        if self.selected_dataset is None:
            print("Please select a dataset first.")
            return

        # Assurer que 'year' est numérique
        self.selected_dataset['year'] = pd.to_numeric(self.selected_dataset['year'], errors='coerce')

        # Lister les années disponibles
        available_years = sorted(self.selected_dataset['year'].unique())
        print("\nAvailable Years:", available_years)

        # Sélection de l’année
        while True:  # Boucle jusqu’à une entrée valide
            try:
                selected_year = int(input("Enter the year for statistics: "))
                if selected_year not in available_years:
                    print("Selected year must be within the available range.")
                    continue
                break
            except ValueError:
                print("Please enter a valid year.")

        # Filtrer les données pour l’année choisie
        year_data = self.selected_dataset[self.selected_dataset['year'] == selected_year]
        print(f"\n--- Summary Statistics for {self.selected_country} ({selected_year}) ---")

        # Calculer les statistiques pour chaque parti
        party_columns = [col for col in year_data.columns if col.startswith('party')]
        result_columns = [col for col in year_data.columns if col.startswith('result') and not col.startswith('final_result')]
        # Boucle sur les colonnes des partis et résultats
        for i, (party_col, result_col) in enumerate(zip(party_columns, result_columns), 1):
            if year_data[party_col].dropna().empty:
                continue  # Passer si la colonne est vide
            party_name = year_data[party_col].dropna().unique()[0]
            party_results = year_data[result_col]
            # Afficher les statistiques
            print(f"\nParty: {party_name}")
            print(f"Mean: {party_results.mean():.2f}%")
            print(f"Median: {party_results.median():.2f}%")
            print(f"Standard Deviation: {party_results.std():.2f}%")
            print(f"Minimum: {party_results.min():.2f}%")
            print(f"Maximum: {party_results.max():.2f}%")

    def manual_data_entry(self):
        """
        Allow manual data entry for a completely new party with all details
        """
        # Méthode pour ajouter manuellement un nouveau parti
        if self.selected_dataset is None:
            print("Please select a dataset first.")
            return

        print("\n--- Manual Data Entry for New Party ---")
        party_name = input("Enter the name of the new party: ")

        # Trouver le prochain index disponible pour les colonnes
        party_columns = [col for col in self.selected_dataset.columns if col.startswith('party')]
        result_columns = [col for col in self.selected_dataset.columns if col.startswith('result') and not col.startswith('final_result')]
        political_leaning_columns = [col for col in self.selected_dataset.columns if col.startswith('political_leaning')]
        final_result_columns = [col for col in self.selected_dataset.columns if col.startswith('final_result')]
        next_index = len(party_columns) + 1

        # Saisie de l’année
        while True:
            try:
                year = int(input("Enter year: "))
                break
            except ValueError:
                print("Please enter a valid year.")

        # Saisie du résultat du sondage
        while True:
            try:
                polling_result = float(input(f"Enter polling result for {party_name} (%): "))
                break
            except ValueError:
                print("Invalid input. Please enter a number.")

        # Saisie de l’orientation politique
        political_leaning = input("Enter political leaning (e.g., Left, Right, Center): ")

        # Saisie du résultat final
        while True:
            try:
                final_result = float(input(f"Enter final result for {party_name} (%): "))
                break
            except ValueError:
                print("Invalid input. Please enter a number.")

        # Créer de nouvelles colonnes si elles n’existent pas
        new_party_col = f'party{next_index}'
        new_result_col = f'result{next_index}'
        new_leaning_col = f'political_leaning{next_index}'
        new_final_result_col = f'final_result{next_index}'

        # Ajouter les nouvelles données
        new_row = pd.DataFrame({
            'year': [year],
            new_party_col: [party_name],
            new_result_col: [polling_result],
            new_leaning_col: [political_leaning],
            new_final_result_col: [final_result]
        })

        # S’assurer que les nouvelles colonnes sont ajoutées au DataFrame
        for col in new_row.columns:
            if col not in self.selected_dataset.columns:
                self.selected_dataset[col] = np.nan

        # Concaténer la nouvelle ligne
        self.selected_dataset = pd.concat([self.selected_dataset, new_row], ignore_index=True)
        print("\nNew party data added successfully!")

    def main_menu(self):
        """
        Main menu for polling dashboard with continuous interaction
        """
        # Menu principal pour naviguer dans l’interface
        while True:  # Boucle infinie pour une interaction continue
            print(f"\n--- {self.selected_country} Polling Dashboard ---")
            print("1. View Polling Trends")
            print("2. Calculate Summary Statistics")
            print("3. Manual Data Entry")
            print("4. Change Dataset")
            print("5. Exit")

            try:
                choice = input("\nSelect an option (1-5): ")
                if choice == '1':
                    self.view_polling_trends()
                elif choice == '2':
                    self.calculate_summary_statistics()
                elif choice == '3':
                    self.manual_data_entry()
                elif choice == '4':
                    self.select_dataset()
                    break  # Retourner à la sélection du dataset
                elif choice == '5':
                    print("Exiting dashboard. Goodbye!")
                    break  # Quitter l’interface
                else:
                    print("Invalid option. Please try again.")
            except Exception as e:
                print(f"An error occurred: {e}")

# Fonction pour lancer l’interface
def main(wide_df, wide2_df):
    """Initialize the CLI dashboard"""
    ElectionPollingCLI(wide_df, wide2_df)  # Créer une instance de l’interface avec les datasets

# To execute: main(wide_df, wide2_df)
# Lancement de l’interface avec les données tchèques et danoises
main(wide_df, wide2_df)


--- Select Dataset ---
1. Czech Republic
2. Denmark
4. Exit


KeyboardInterrupt: Interrupted by user